<h1>
    <center>B-Cycle Vehicles Austin</center>
</h1>
<h2>
    <center>Team: Data Vaders</center>
    <h4>
        <center>Zarif Choudhury</center>
        <center>Vaidehi Durape</center>
        <center>Aashima Garg</center>
        <center>Aneesh Soni</center>
        <center>Brian Wilmarth</center>
    </h4>
</h2>

# Libraries Used

In [1]:
import pandas as pd
import numpy as np
import seaborn as sns
import matplotlib
import warnings
from datetime import date
import folium
from folium.plugins import HeatMap
from folium.plugins import HeatMapWithTime
import cufflinks as cf
cf.go_offline()
import plotly
import plotly.plotly as py
import plotly.graph_objs as go
plotly.tools.set_credentials_file(username='aneeshsoni', api_key='e9PuzLMTHBbA5eVvZVNr')
warnings.filterwarnings('ignore')
mapbox_access_token = 'pk.eyJ1IjoiYW5lZXNoc29uaSIsImEiOiJjanZyOW1kemQwZnhwM3lueHhiZDE4ZTcwIn0.iywNpoytj-XU17BF4Tp_Fw'

import matplotlib.pyplot as plt
from scipy.stats import skew
from scipy.stats.stats import pearsonr
from sklearn.linear_model import Ridge, RidgeCV, ElasticNet, LassoCV, LassoLarsCV
from sklearn.model_selection import cross_val_score
from sklearn.ensemble import (RandomForestClassifier, AdaBoostClassifier, GradientBoostingClassifier, ExtraTreesClassifier)
from sklearn.svm import SVC
from IPython.display import HTML, display, IFrame

%config InlineBackend.figure_format = 'png' #set 'png' here when working on notebook
%matplotlib inline

In [2]:
def generateBaseMap(default_location=[30.2672, -97.7431], default_zoom_start=12):
    base_map = folium.Map(location=default_location, control_scale=True, zoom_start=default_zoom_start)
    return base_map

# Load Data

In [19]:
b_cycle = pd.read_csv("./Data/Austin_B-Cycle_Trips.csv")

# B-Cycle Data

### Summary of Data
- 1,077,929 total trips recorded

### Formatting and Cleaning Data

Only looking at data from 2018 to 2019

In [20]:
b_cycle['Checkout Date'] = pd.to_datetime(b_cycle['Checkout Date'], format='%m/%d/%Y')

b_cycle = b_cycle.loc[b_cycle['Checkout Date'].between('2018-01-01','2019-01-01', inclusive=True)]

In [21]:
b_cycle.head()

Trip ID      Membership Type  Bicycle ID Checkout Date Checkout Time  \
719724  16555367                  NaN       272.0    2018-01-03      11:12:36   
719854  16551622             Local365       709.0    2018-01-01       0:39:02   
719855  16551639              Walk Up      1000.0    2018-01-01       1:17:54   
719856  16551677              Walk Up       919.0    2018-01-01       5:05:52   
719857  16551764  Local365+Guest Pass       871.0    2018-01-01       9:17:24   

        Checkout Kiosk ID                     Checkout Kiosk  Return Kiosk ID  \
719724             3292.0                  East 4th & Chicon           3292.0   
719854             2494.0                     2nd & Congress           2563.0   
719855             2494.0                     2nd & Congress           2548.0   
719856             2539.0  Convention Center / 3rd & Trinity           2539.0   
719857             2563.0             Davis at Rainey Street           3621.0   

                             Return Kiosk  Trip Duration Minutes  Month  Year  
719724                  East 4th & Chicon                      0    NaN   NaN  
719854             Davis at Rainey Street                      6    NaN   NaN  
719855           UT West Mall @ Guadalupe                    416    NaN   NaN  
719856  Convention Center / 3rd & Trinity                      1    NaN   NaN  
719857                       Nueces & 3rd                      8    NaN   NaN

### Understanding Data

#### Trip Duration (2018)

In [23]:
trace1 = go.Histogram(
    x=b_cycle['Trip Duration Minutes'],
    opacity=0.8,
    xbins=dict(
        start=0,
        end=200
    )
)

data = [trace1]
layout = go.Layout(
            barmode='overlay',
            title='Trip Duration',
                xaxis=dict(
                    title='Trip Duration (Minutes)',
                    titlefont=dict(
                        size=14,
                    ),

                ),
                yaxis=dict(
                    title='Number of Trips',
                    titlefont=dict(
                        size=14,
                    )
                )
            )

plotly.offline.plot(data, filename='./Visualizations/Trip Duration B-Cycle.html', auto_open = False)
fig = go.Figure(data=data, layout=layout)
plotly.offline.iplot(fig, filename = 'Trip Duration B-Cycle')

In [25]:
start = date(2018,1,1)
end = date(2018,10,31)
days = (end - start).days

b_cycle_rides_per_day = len(b_cycle)/days

In [26]:
data = [['B-Cycle', b_cycle_rides_per_day]] 
df = pd.DataFrame(data, columns = ['Mode of Transportation', 'Rides Per Day']) 

trace1 = go.Bar(
    x = df['Mode of Transportation'],
    y = df['Rides Per Day'],
    marker=dict(
        color=['rgb(18, 97, 160)'])
)

data = [trace1]

layout = go.Layout(
    title='Average Rides Per Day',
    xaxis=dict(
        title='Mode of Transportation',
        titlefont=dict(
            size=14,
            color='rgb(107, 107, 107)'
        ),
        tickfont=dict(
            size=14
        )
    ),
    yaxis=dict(
        title='Rides Per Day',
        titlefont=dict(
            size=14,
            color='rgb(107, 107, 107)'
        )
    )
)

plotly.offline.plot(data, filename='./Visualizations/Rides_Per_Day_B_Cycle.html', auto_open = False)
fig = go.Figure(data=data, layout=layout)
plotly.offline.iplot(fig, filename = 'Rides Per Day B-Cycle')

In [269]:
data = [['Downtown', downtown_avg_distance], ['SoCo & Zilker', soco_zilker_avg_distance], ['West Campus', west_campus_avg_distance]] 
df = pd.DataFrame(data, columns = ['Location', 'Ride Distance']) 

trace1 = go.Bar(
    x = df['Location'],
    y = df['Ride Distance'],
    marker=dict(
        color=['rgb(18, 97, 160)', 'rgb(56, 149, 211)',
               'rgb(88, 204, 237)'])
)

data = [trace1]

layout = go.Layout(
    title='Average Ride Distance',
    xaxis=dict(
        title='Location',
        titlefont=dict(
            size=14,
            color='rgb(107, 107, 107)'
        ),
        tickfont=dict(
            size=14
        )
    ),
    yaxis=dict(
        title='Ride Distance (Meters)',
        titlefont=dict(
            size=14,
            color='rgb(107, 107, 107)'
        )
    ),
)

plotly.offline.plot(data, filename='./Visualizations/Ride_Distance.html', auto_open = False)
fig = go.Figure(data=data, layout=layout)
plotly.offline.iplot(fig, filename = 'Ride Distance')

In [270]:
data = [['Downtown', downtown_avg_time], ['SoCo & Zilker', soco_zilker_avg_time], ['West Campus', west_campus_avg_time]] 
df = pd.DataFrame(data, columns = ['Location', 'Ride Duration']) 

trace1 = go.Bar(
    x = df['Location'],
    y = df['Ride Duration'],
    marker=dict(
        color=['rgb(18, 97, 160)', 'rgb(56, 149, 211)',
               'rgb(88, 204, 237)'])
)

data = [trace1]

layout = go.Layout(
    title='Average Ride Duration',
    xaxis=dict(
        title='Location',
        titlefont=dict(
            size=14,
            color='rgb(107, 107, 107)'
        ),
        tickfont=dict(
            size=14
        )
    ),
    yaxis=dict(
        title='Ride Duration (Seconds)',
        titlefont=dict(
            size=14,
            color='rgb(107, 107, 107)'
        )
    ),
)

plotly.offline.plot(data, filename='./Visualizations/Ride_Duration.html', auto_open = False)
fig = go.Figure(data=data, layout=layout)
plotly.offline.iplot(fig, filename = 'Ride Duration')

### Average Idle Time for Each Scooter

- see how long on average a scooter is idle in each location
- compare to all data
- not possible to compute given the data given to us was in intervals of 15 mins

In [ ]:
# Select all duplicate rows based on one column
same_downtown = downtown[downtown.duplicated(['Device ID', 'Month', 'Day of Week'])]
same_soco_zilker = soco_zilker[soco_zilker.duplicated(['Device ID', 'Month', 'Day of Week'])]
same_west_campus = west_campus[west_campus.duplicated(['Device ID', 'Month', 'Day of Week'])]

same_downtown = same_downtown.sort_values(['Device ID', 'Start Time', 'Hour'], ascending=[True, True, True])
same_soco_zilker = same_soco_zilker.sort_values(['Device ID', 'Start Time', 'Hour'], ascending=[True, True, True])
same_west_campus = same_west_campus.sort_values(['Device ID', 'Start Time', 'Hour'], ascending=[True, True, True])

same_downtown.reset_index(drop=True)
same_soco_zilker.reset_index(drop=True)
same_west_campus.reset_index(drop=True)